In [ ]:
import re
import csv
import pandas
import sqlite3
import random
import json
import itertools
import numpy as np
from sumeval.metrics.rouge import RougeCalculator
rouge = RougeCalculator(stopwords=False, lang="en")

from utils import *

In [ ]:
db_file = 'mimic_db/mimic.db'
model = query(db_file)
(db_meta, db_tabs, db_head) = model._load_db(db_file)

In [ ]:
headerDic = []
for tb in db_head:
    for hd in db_head[tb]:
        headerDic.append('.'.join([tb, hd]).lower())
# print(headerDic)
tableDic = []
for tb in db_head:
    tableDic.append(tb.lower())
# print(tableDic)

In [ ]:
def parse_sql(sql):
    
    sqlForm = {}
    
    arr = re.split('where', sql)
    qlead = re.split('from', arr[0])
    qagg = re.split('\s', qlead[0])
    qagg = list(filter(None, qagg))
    if qagg[1] == 'count' or qagg[1] == 'min' or qagg[1] == 'max' or qagg[1] == 'avg':
        sqlForm['sel'] = qagg[1]
    else:
        sqlForm['sel'] = ''
        
    itm = []
    for wd in qagg:
        if wd in headerDic:
            itm.append(wd)
    sqlForm['agg'] = itm
    
    itm = []
    qtab = re.split('\s', qlead[1])
    qtab = list(filter(None, qtab))
    for wd in qtab:
        if wd in tableDic:
            itm.append(wd)
    sqlForm['tab'] = itm
        
    qtail = re.split('and', arr[-1])
    itm = []
    for cond in qtail:
        cond = re.split('\s', cond)
        cond = list(filter(None, cond))
        if len(cond) > 2:
            condVal = ' '.join(cond[2:])
            condVal = re.split('\"|\s', condVal)
            condVal = ' '.join(list(filter(None, condVal)))
            itm.append(cond[:2] + [condVal])
    sqlForm['cond'] = sorted(itm)
    
    return sqlForm

fp = open('generated_sql/output.json', 'r')
outGen = []
outTtt = []
for line in fp:
    line = json.loads(line)
    gen = re.split('<stop>', line['sql_pred'])[0]
    sqlG = parse_sql(gen)
    outGen.append(sqlG)
    
    ttt = line['sql_gold']
    sqlT = parse_sql(ttt)
    outTtt.append(sqlT)
#     print(sqlG)
#     print(sqlT)
#     break
fp.close()

In [ ]:
cnt = 0
for k in range(len(outGen)):
    if outGen[k] == outTtt[k]:
        cnt += 1
print('Overall logic form accuracy: {}'.format(cnt/1000))

## Aggregation

In [ ]:
cnt = 0
for k in range(len(outGen)):
    if outGen[k]['sel'] == outTtt[k]['sel']:
        cnt += 1
print('Break-down accuracy on AGGREGATION OPERATION: {}'.format(cnt/1000))

In [ ]:
cnt = 0
for k in range(len(outGen)):
    if outGen[k]['agg'] == outTtt[k]['agg']:
        cnt += 1
print('Break-down accuracy on AGGREGATION COLUMN: {}'.format(cnt/1000))

## Table

In [ ]:
cnt = 0
for k in range(len(outGen)):
    if outGen[k]['tab'] == outTtt[k]['tab']:
        cnt += 1
print('Break-down accuracy on TABLE: {}'.format(cnt/1000))

## Condition

In [ ]:
cnt = 0
for k in range(len(outGen)):
    arrG = [wd[0] for wd in outGen[k]['cond']]
    arrT = [wd[0] for wd in outTtt[k]['cond']]
    if arrG == arrT:
        cnt += 1
print(cnt)

In [ ]:
cnt = 0
for k in range(len(outGen)):
    arrG = [wd[:2] for wd in outGen[k]['cond']]
    arrT = [wd[:2] for wd in outTtt[k]['cond']]
    if arrG == arrT:
        cnt += 1
print('Break-down accuracy on CONDITION COLUMN AND OPERATION: {}'.format(cnt/1000))

In [ ]:
cnt = 0
for k in range(len(outGen)):
    arrG = [wd[:3] for wd in outGen[k]['cond']]
    arrT = [wd[:3] for wd in outTtt[k]['cond']]
    if arrG == arrT:
        cnt += 1
print('Break-down accuracy on CONDITION VALUE: {}'.format(cnt/1000))